In [8]:
import sys
import os
import SimpleITK
import numpy
import matplotlib.pyplot
import chardet
import json
sys.path.append(os.path.join(os.path.expanduser('~'),'software','src','nixSuite','wrapper'))
import nixWrapper
nixWrapper.loadLibrary('labkeyInterface')
import labkeyInterface
net=labkeyInterface.labkeyInterface()
fconfig=os.path.join(os.path.expanduser('~'),'.labkey','network.json')
net.init(fconfig)
print('Using: {}'.format(net.connectionConfig['SSL']['user']))
net.getCSRF()
import labkeyFileBrowser
sys.path.append(os.getcwd())
fb=labkeyFileBrowser.labkeyFileBrowser(net)
project='iPNUMMretro/Study'
import labkeyDatabaseBrowser
db=labkeyDatabaseBrowser.labkeyDB(net)
ds=db.selectRows(project,'study','ClinicalData',[])
patients=[row['PatientId'] for row in ds['rows']]


Using: /home/studen/.labkey/astuden/astuden.crt


/usr/lib/python3/dist-packages/urllib3/connection.py:391: SubjectAltNameWarning: Certificate for merlin.fmf.uni-lj.si has no `subjectAltName`, falling back to check for a `commonName` for now. This feature is being removed by major browsers and deprecated by RFC 2818. (See https://github.com/urllib3/urllib3/issues/497 for details.)
  warnings.warn(


User: andrej studen CSRF: 52cd68383b7a832e93e7d9b5801002e5


In [61]:
rows=ds['rows']
for row in rows:
    idFilter={'variable':'PatientId','value':row['PatientId'],'oper':'eq'}
    dsQ=db.selectRows(project,'study','ClinicalDataInternational',[idFilter])
    
    if len(dsQ['rows'])==0:
        fields=['PatientId','SequenceNum']
        qrow={f:row[f] for f in fields}
        mode='insert' 
    else:
        qrow=dsQ['rows'][0]
        mode='update'
    
    copyFields=['itStartAge']
    for f in copyFields:
        qrow[f]=row[f]
    
    if row['sex']==0:
        qrow['gender']=1
    if row['sex']==1:
        qrow['gender']=2
    qrow['aeStartDate']=row['aeIdentificationDate']
    
    if row['origoCode']==0:
        qrow['melanomaPrimaryAnatomicSite']=3
    if row['origoCode']==1:
        qrow['melanomaPrimaryAnatomicSite']=1
    if row['origoCode']==2:
        qrow['melanomaPrimaryAnatomicSite']=2
    if row['origoCode']==3:
        qrow['melanomaPrimaryAnatomicSite']=4
    
    qrow['psECOGStartIT']=row['psAtITIntroduction']
    if row['mutations']==0:
        qrow ['actionableMutation']=1
    if row['mutations']==1:
        qrow ['actionableMutation']=2
    if row['mutations']==2:
        qrow ['actionableMutation']=3
    if row['mutations']==3:
        qrow ['actionableMutation']=4
    if row['mutations']==9:
        qrow ['actionableMutation']=5
        
    qrow['itTreatmentSetting']=2
    qrow['itStartDate']=row['itStart']
    qrow['firstITStartDate']=row['itStart']
    
    if row['bora']==0:#CR
        qrow ['bestResponse']=4
    if row['bora']==1:#PR
        qrow ['bestResponse']=2 #radiographic response
    if row['bora']==2:#SD
        qrow ['bestResponse']=3 #mixed radiographic response
    if row['bora']==9:#PD
        qrow ['bestResponse']=1
    
    if row['pneumonitis']==0:
        qrow['pneumonitisGrade']=7
    else:
        qrow['pneumonitisGrade']=row['pneumonitis']
        qrow['pneumonitisDate']=row['aeIdentificationDate']
        
    
    if row['diarrhea']=="0":
        qrow['colitisGrade']=7
    else:
        qrow['colitisGrade']=row['diarrhea']
        qrow['colitisDate']=row['aeIdentificationDate']
        
        
    if row['hypotirosis']==0:
        qrow['thyroiditisGrade']=7
    else:
        qrow['thyroiditisGrade']=row['hypotirosis']
        qrow['thyroiditisDate']=row['aeIdentificationDate']
        
    
    if row['sistemicKS']==0:
        qrow['immunosupressionFlag']=2
    if row['sistemicKS']==1:
        qrow['immunosupressionFlag']=1
    
    qrow['firstITInfusionDate']=row['itStart']
    qrow['itLine']=2
    #qrow['durationOfCurrentIT']=
    
    statusResponse=db.modifyRows(mode,project,'study','ClinicalDataInternational',[qrow])
    encoding=chardet.detect(statusResponse)['encoding']
    status=json.loads(statusResponse.decode(encoding))
    try:
        print('{}: {}'.format(row['PatientId'],status['exception']))
    except KeyError:
        pass
    #qrow['itType']=

    

/usr/lib/python3/dist-packages/urllib3/connection.py:391: SubjectAltNameWarning: Certificate for merlin.fmf.uni-lj.si has no `subjectAltName`, falling back to check for a `commonName` for now. This feature is being removed by major browsers and deprecated by RFC 2818. (See https://github.com/urllib3/urllib3/issues/497 for details.)
  warnings.warn(


User: andrej studen CSRF: da3766ebe339095e3a6098173e1021be
User: andrej studen CSRF: f6a2f89d2f85bab544539a2a6369623f
User: andrej studen CSRF: 9f326c3dcb4b44d6a7e5ab4f8a7ad8e5
NIX-LJU-D2002-IRAE-A002: Row 1 Could not convert 'Brez simptomov' for field pneumonitisDate, should be of type Timestamp


/usr/lib/python3/dist-packages/urllib3/connection.py:391: SubjectAltNameWarning: Certificate for merlin.fmf.uni-lj.si has no `subjectAltName`, falling back to check for a `commonName` for now. This feature is being removed by major browsers and deprecated by RFC 2818. (See https://github.com/urllib3/urllib3/issues/497 for details.)
  warnings.warn(


User: andrej studen CSRF: 23dc8fd59e280d53b02bbe070154ddfd
User: andrej studen CSRF: a5262b1412a1eee7c4b89b1125cae433
User: andrej studen CSRF: 43860ad987c603df25731d108a6f8001
User: andrej studen CSRF: af866c8085460ff91530b735e3c736dd
User: andrej studen CSRF: 24f34a00e4376366740efe2e187fa4e2
User: andrej studen CSRF: 933ce18a272115a2183d751a91dba4e3
User: andrej studen CSRF: cf62df2f5e93ae8f4585e1180edd81d2
User: andrej studen CSRF: 35fbfe403566416581defd2efb709fba
User: andrej studen CSRF: f73fbbe1e541cd5ede1ff09b7f5807be
User: andrej studen CSRF: 882aac6ea404860faab770ae320df827
User: andrej studen CSRF: bfdb52f52cae66c27d88d93dc2dbe2bf
User: andrej studen CSRF: 3c48c8bec64e886deb27ee07d7f100c7
NIX-LJU-D2002-IRAE-A014: Row 1 Could not convert '2 (bolj gradus 1)' for field colitisGrade, should be of type Integer


/usr/lib/python3/dist-packages/urllib3/connection.py:391: SubjectAltNameWarning: Certificate for merlin.fmf.uni-lj.si has no `subjectAltName`, falling back to check for a `commonName` for now. This feature is being removed by major browsers and deprecated by RFC 2818. (See https://github.com/urllib3/urllib3/issues/497 for details.)
  warnings.warn(


User: andrej studen CSRF: 753d6094324a2cf7b0c2183a58efc7f5
User: andrej studen CSRF: f062199d4b6f0ae27c79ae8419d14d78
User: andrej studen CSRF: 008a3f6d93aa90095b3583f755820351
User: andrej studen CSRF: afdb1f8aaf40d60beaba5b3bdb7a1e5e
User: andrej studen CSRF: eaf924935c314c9e900ee44e4cfbc01f
User: andrej studen CSRF: a4bbb057b0b857b171f1d64df73f4ece
User: andrej studen CSRF: 762f91b1c9d5660a47e9db009c5ef3dd
User: andrej studen CSRF: b4bf09d3c6253cf1778cf469ae44e835
User: andrej studen CSRF: efb18145b40fc1f1bd11eb1453d29eef
User: andrej studen CSRF: 850ae1edf1e364273f7a61a115e3a6b1
User: andrej studen CSRF: b776dca81c5e8a4229c1cfaf9271e14a
User: andrej studen CSRF: 8beff4a7833d3ab9038e39b03e10a6ce
User: andrej studen CSRF: 9ff9519885f76f6915d9882745416f3c
User: andrej studen CSRF: 6d04cf5aa9301790c5f88f358f016954
User: andrej studen CSRF: e6340e8bded2d34150a4c897288477af
User: andrej studen CSRF: 351d0f95a8414060f042fd76a6668417


In [28]:
dset='ClinicalDataInternational'
#dset='Imaging1'
idFilter={'variable':'PatientId','value':'NIX-LJU-D2002-IRAE-A014','oper':'eq'}
ds=db.selectRows(project,'study',dset,[idFilter])

rows=ds['rows']
for row in rows:
   print('{}:{}',row['PatientId'],row['valid'])
   row['valid']=0
   db.modifyRows('update',project,'study',dset,[row])    
        

{}:{} NIX-LJU-D2002-IRAE-A014 True
User: andrej studen CSRF: 14eef5230ef9055ca662e626545b47a3


In [7]:
rows=ds['rows']
for row in rows:
    idFilter={'variable':'PatientId','value':row['PatientId'],'oper':'eq'}
    dsQ=db.selectRows(project,'study','ClinicalDataInternational',[idFilter])
    
    vals={'petDetectedAE':2,'earlyPETAEDetection':2,'petRelatedAction':2}#No
    for v in vals:
        print(row[v])
        if row[v]=='DA':
            vals[v]=1 #Yes
    for qrow in dsQ['rows']:
        print('ID: {}'.format(qrow['PatientId']))
        for v in vals:
            qrow[v]=vals[v]
            print('{}: {}'.format(v,qrow[v]))
    db.modifyRows('update',project,'study','ClinicalDataInternational',[qrow])    
        

/usr/lib/python3/dist-packages/urllib3/connection.py:391: SubjectAltNameWarning: Certificate for merlin.fmf.uni-lj.si has no `subjectAltName`, falling back to check for a `commonName` for now. This feature is being removed by major browsers and deprecated by RFC 2818. (See https://github.com/urllib3/urllib3/issues/497 for details.)
  warnings.warn(


None
None
None
ID: NIX-LJU-D2002-IRAE-A000
petDetectedAE: 2
earlyPETAEDetection: 2
petRelatedAction: 2
User: andrej studen CSRF: e6ddccd420b2c45a98f4448be951ccef
DA
NE
N/A
ID: NIX-LJU-D2002-IRAE-A001
petDetectedAE: 1
earlyPETAEDetection: 2
petRelatedAction: 2
User: andrej studen CSRF: 9e7dbdb1cdac31d0864826f400101393
DA
DA
DA
ID: NIX-LJU-D2002-IRAE-A002
petDetectedAE: 1
earlyPETAEDetection: 1
petRelatedAction: 1
User: andrej studen CSRF: c0bbc36da5070408e01f64bab3080f1b
None
None
None
ID: NIX-LJU-D2002-IRAE-A003
petDetectedAE: 2
earlyPETAEDetection: 2
petRelatedAction: 2
User: andrej studen CSRF: e7ca4b3cd6c8d27d543fff197b90a032
DA
DA
DA
ID: NIX-LJU-D2002-IRAE-A004
petDetectedAE: 1
earlyPETAEDetection: 1
petRelatedAction: 1
User: andrej studen CSRF: fa458a4c0e96331402bdd87f8a7f710a
NE?
?
N/A
ID: NIX-LJU-D2002-IRAE-A005
petDetectedAE: 2
earlyPETAEDetection: 2
petRelatedAction: 2
User: andrej studen CSRF: 59fb9bedb5feef9f13b413f6c8c5df38
None
None
None
ID: NIX-LJU-D2002-IRAE-A006
petDete